# VacationPy
----

#### Note
* Instructions have been included for each segment. You do not have to follow them exactly, but they are included to help you think through the steps.

In [3]:
# Dependencies and Setup
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import requests
import gmaps
import os
import json

# Import API key
from api_keys import g_key


### Store Part I results into DataFrame
* Load the csv exported in Part I to a DataFrame

In [4]:
cities_data = "../output_data/cities.csv"
cities_df=pd.read_csv(cities_data )
cities_df

City    Lat     Lng  Max Temp  Humidity  Cloudiness  \
0         coihaique -45.58  -72.07     13.00        62          75   
1           rikitea -23.12 -134.97     25.63        84          67   
2           kahului  20.89 -156.47     26.00        69          75   
3       santa maria -29.68  -53.81     20.77        57           9   
4        manzanillo  20.34  -77.12     33.14        38           0   
..              ...    ...     ...       ...       ...         ...   
596           farah  32.50   62.50     18.76        44         100   
597  campbell river  50.02 -125.24     15.00        13           5   
598        zyryanka  65.75  150.85     -3.97        97          99   
599        westport  41.14  -73.36     17.00        58           1   
600             edd  13.93   41.69     26.75        73          94   

     Wind Speed Country        Date  
0          2.60      CL  1586729388  
1          6.91      PF  1586729324  
2          5.10      US  1586729106  
3          1.98      BR  1586729537  
4          1.86      CU  1586729784  
..          ...     ...         ...  
596        1.74      AF  1586730468  
597        3.10      CA  1586730469  
598        2.95      RU  1586730470  
599        4.10      US  1586730429  
600        3.41      ER  1586730472  

[601 rows x 9 columns]

### Humidity Heatmap
* Configure gmaps.
* Use the Lat and Lng as locations and Humidity as the weight.
* Add Heatmap layer to map.

In [22]:
gmaps.configure(api_key=g_key)


In [5]:

locations = cities_df[["Lat","Lng"]].astype(float)
#cities_df_clean = cities_df.dropna()
#Humidity_clean =cities_df_clean["Humidity"].astype(float)
Humidity_value =cities_df["Humidity"].astype(float)
Humidity_value

0      62.0
1      84.0
2      69.0
3      57.0
4      38.0
       ... 
596    44.0
597    13.0
598    97.0
599    58.0
600    73.0
Name: Humidity, Length: 601, dtype: float64

In [6]:
fig = gmaps.figure()
heat_layer = gmaps.heatmap_layer(locations, weights=Humidity_value, 
                                 dissipating=False, max_intensity=100,
                                 point_radius = 1)

fig.add_layer(heat_layer)
fig

Figure(layout=FigureLayout(height='420px'))

### Create new DataFrame fitting weather criteria
* Narrow down the cities to fit weather conditions.
* Drop any rows will null values.

In [8]:
cities_good_weather = cities_df.loc[(cities_df["Max Temp"] <25) & (cities_df["Max Temp"]>10), [
    "City", "Lat","Lng","Max Temp","Humidity","Cloudiness","Wind Speed","Country","Date" ]]
cities_good_weather_clean = cities_good_weather.dropna()
cities_good_weather_clean

City    Lat     Lng  Max Temp  Humidity  Cloudiness  \
0         coihaique -45.58  -72.07     13.00        62          75   
3       santa maria -29.68  -53.81     20.77        57           9   
6         springbok -29.66   17.89     12.12        72           0   
10           albany  42.60  -73.97     17.22        25          75   
11        carnarvon -24.87  113.63     24.00       100           2   
..              ...    ...     ...       ...       ...         ...   
594   saint andrews  34.05  -81.13     20.00        93          90   
595           basco  20.45  121.97     20.50        78          99   
596           farah  32.50   62.50     18.76        44         100   
597  campbell river  50.02 -125.24     15.00        13           5   
599        westport  41.14  -73.36     17.00        58           1   

     Wind Speed Country        Date  
0          2.60      CL  1586729388  
3          1.98      BR  1586729537  
6          0.95      ZA  1586729763  
10         7.20      US  1586729502  
11         7.20      AU  1586729528  
..          ...     ...         ...  
594        5.10      US  1586730467  
595       11.43      PH  1586730468  
596        1.74      AF  1586730468  
597        3.10      CA  1586730469  
599        4.10      US  1586730429  

[229 rows x 9 columns]

### Hotel Map
* Store into variable named `hotel_df`.
* Add a "Hotel Name" column to the DataFrame.
* Set parameters to search for hotels with 5000 meters.
* Hit the Google Places API for each city's coordinates.
* Store the first Hotel result into the DataFrame.
* Plot markers on top of the heatmap.

In [9]:
hotel_df = cities_good_weather_clean[["City", "Lat","Lng","Country"]].copy()
hotel_df["hotels"] =" "
hotel_df
params = {
    "radius": 5000,
    "types": "lodging",
    "key": g_key
}
for index, row in hotel_df.iterrows():

    lat = row['Lat']
    long =row['Lng']
    #Params["location"]=f'{lat},{long}'
    base_url = f'https://maps.googleapis.com/maps/api/place/nearbysearch/json?location={lat},{long}'
    response = requests.get(base_url, params=params)
    places_data = response.json()
    #print(response.json()['results'])
    print(json.dumps(places_data['results'], indent=4, sort_keys=True))
    try:
        hotel_df.loc[index, 'hotels'] = places_data['results'][0]['name']
    except (KeyError, IndexError):
        print("Missing field/result... skipping.")
        pass
        
    

[
    {
        "geometry": {
            "location": {
                "lat": -45.5840482,
                "lng": -72.0747257
            },
            "viewport": {
                "northeast": {
                    "lat": -45.5827132697085,
                    "lng": -72.0733364697085
                },
                "southwest": {
                    "lat": -45.5854112302915,
                    "lng": -72.0760344302915
                }
            }
        },
        "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/lodging-71.png",
        "id": "43b6b5fe13f3ea7eeaeb6d22a3a7be40ad400c59",
        "name": "Diego De Almagro Coyhaique",
        "photos": [
            {
                "height": 2304,
                "html_attributions": [
                    "<a href=\"https://maps.google.com/maps/contrib/107057214343137139162\">Pablo Maldonado P.</a>"
                ],
                "photo_reference": "CmRaAAAAnd48TZOVqLBnoKoVp62thjqrZ_gngiIA_8tPUmQrq11AqJ-3l2C7CN

[
    {
        "geometry": {
            "location": {
                "lat": -29.68590199999999,
                "lng": -53.804817
            },
            "viewport": {
                "northeast": {
                    "lat": -29.6845056697085,
                    "lng": -53.80348351970851
                },
                "southwest": {
                    "lat": -29.6872036302915,
                    "lng": -53.80618148029151
                }
            }
        },
        "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/lodging-71.png",
        "id": "b9ee7ec3d5198e9f3c11f3c227f54c83c31d3c73",
        "name": "Hotel Morotin",
        "opening_hours": {
            "open_now": true
        },
        "photos": [
            {
                "height": 4288,
                "html_attributions": [
                    "<a href=\"https://maps.google.com/maps/contrib/112727889629438973982\">Morotin</a>"
                ],
                "photo_reference": "CmRaAAAAvGR

[
    {
        "geometry": {
            "location": {
                "lat": -29.650689,
                "lng": 17.88424
            },
            "viewport": {
                "northeast": {
                    "lat": -29.6494140697085,
                    "lng": 17.8854710802915
                },
                "southwest": {
                    "lat": -29.6521120302915,
                    "lng": 17.8827731197085
                }
            }
        },
        "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/lodging-71.png",
        "id": "acabaa488820cd39238dbc1c0674c31300f90bbc",
        "name": "Faithful Guest Lodge",
        "opening_hours": {
            "open_now": false
        },
        "photos": [
            {
                "height": 2268,
                "html_attributions": [
                    "<a href=\"https://maps.google.com/maps/contrib/107429913088791068471\">Werner Oosthuizen</a>"
                ],
                "photo_reference": "CmRaAAA

[]
Missing field/result... skipping.
[
    {
        "geometry": {
            "location": {
                "lat": -24.8923413,
                "lng": 113.6550343
            },
            "viewport": {
                "northeast": {
                    "lat": -24.8908981697085,
                    "lng": 113.6564608802915
                },
                "southwest": {
                    "lat": -24.8935961302915,
                    "lng": 113.6537629197085
                }
            }
        },
        "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/lodging-71.png",
        "id": "ee38d0465d4fe139a0960514cdd3a2894bdfc1b5",
        "name": "Hospitality Carnarvon",
        "opening_hours": {
            "open_now": false
        },
        "photos": [
            {
                "height": 3024,
                "html_attributions": [
                    "<a href=\"https://maps.google.com/maps/contrib/100431928530236451406\">kimera Ogame</a>"
                ],
    

[
    {
        "geometry": {
            "location": {
                "lat": 41.4113711,
                "lng": -73.4152646
            },
            "viewport": {
                "northeast": {
                    "lat": 41.4126229802915,
                    "lng": -73.4140460697085
                },
                "southwest": {
                    "lat": 41.4099250197085,
                    "lng": -73.41674403029151
                }
            }
        },
        "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/lodging-71.png",
        "id": "46baeac90de21c083bad16d9cbb7486fca98fd6f",
        "name": "Courtyard by Marriott Danbury",
        "opening_hours": {
            "open_now": true
        },
        "photos": [
            {
                "height": 1366,
                "html_attributions": [
                    "<a href=\"https://maps.google.com/maps/contrib/105731878337185886845\">Courtyard by Marriott Danbury</a>"
                ],
                "ph

...

[
    {
        "geometry": {
            "location": {
                "lat": -22.00083,
                "lng": -48.38855
            },
            "viewport": {
                "northeast": {
                    "lat": -21.9994473697085,
                    "lng": -48.3872038697085
                },
                "southwest": {
                    "lat": -22.0021453302915,
                    "lng": -48.3899018302915
                }
            }
        },
        "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/lodging-71.png",
        "id": "f8abde209593d5aee68116ad20aba19aaec267dc",
        "name": "Pousada do Ip\u00ea",
        "opening_hours": {
            "open_now": true
        },
        "photos": [
            {
                "height": 1536,
                "html_attributions": [
                    "<a href=\"https://maps.google.com/maps/contrib/117263506830048758310\">Pousada do Ip\u00ea</a>"
                ],
                "photo_reference": "CmRaA

[
    {
        "geometry": {
            "location": {
                "lat": 34.0331272,
                "lng": -81.1093309
            },
            "viewport": {
                "northeast": {
                    "lat": 34.0346225802915,
                    "lng": -81.10801961970851
                },
                "southwest": {
                    "lat": 34.0319246197085,
                    "lng": -81.11071758029152
                }
            }
        },
        "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/lodging-71.png",
        "id": "737db1c57bdebc11ed34ca7e7155f680d536a23d",
        "name": "Baymont by Wyndham Columbia Northwest",
        "opening_hours": {
            "open_now": true
        },
        "photos": [
            {
                "height": 400,
                "html_attributions": [
                    "<a href=\"https://maps.google.com/maps/contrib/102094091177425657574\">Baymont by Wyndham Columbia Northwest</a>"
                ],
   

[
    {
        "geometry": {
            "location": {
                "lat": 20.44701419999999,
                "lng": 121.9704848
            },
            "viewport": {
                "northeast": {
                    "lat": 20.4483775802915,
                    "lng": 121.9718583802915
                },
                "southwest": {
                    "lat": 20.4456796197085,
                    "lng": 121.9691604197085
                }
            }
        },
        "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/lodging-71.png",
        "id": "f83143ae04473fa77ccb9da8a0144a1acdc27d50",
        "name": "Nathaniel's Lodge",
        "photos": [
            {
                "height": 1457,
                "html_attributions": [
                    "<a href=\"https://maps.google.com/maps/contrib/104300773896259208849\">Nathaniel&#39;s Lodge</a>"
                ],
                "photo_reference": "CmRaAAAAT4S937s_z_rICzSRaTGTOcnrj00E2d59PAXk74jN2EbBGYi7yIjsPZ9W

[]
Missing field/result... skipping.
[
    {
        "geometry": {
            "location": {
                "lat": 49.9992984,
                "lng": -125.2309703
            },
            "viewport": {
                "northeast": {
                    "lat": 50.0006656802915,
                    "lng": -125.2293419197085
                },
                "southwest": {
                    "lat": 49.99796771970851,
                    "lng": -125.2320398802915
                }
            }
        },
        "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/lodging-71.png",
        "id": "82fea5eb236150e36770d8b9bda606bc5adf77ec",
        "name": "Ramada by Wyndham Campbell River",
        "opening_hours": {
            "open_now": true
        },
        "photos": [
            {
                "height": 1969,
                "html_attributions": [
                    "<a href=\"https://maps.google.com/maps/contrib/110002158656987762821\">Ramada by Wyndham Campbell Riv

[
    {
        "geometry": {
            "location": {
                "lat": 41.1389728,
                "lng": -73.30889499999999
            },
            "viewport": {
                "northeast": {
                    "lat": 41.1402740302915,
                    "lng": -73.3072082697085
                },
                "southwest": {
                    "lat": 41.1375760697085,
                    "lng": -73.3099062302915
                }
            }
        },
        "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/lodging-71.png",
        "id": "4e43df2b352b17006d24c9634ac9e82b95e7477c",
        "name": "The Westport Inn",
        "opening_hours": {
            "open_now": true
        },
        "photos": [
            {
                "height": 1365,
                "html_attributions": [
                    "<a href=\"https://maps.google.com/maps/contrib/114963843917944334453\">The Westport Inn</a>"
                ],
                "photo_reference": "CmR

In [10]:
hotel_df

City    Lat     Lng Country  \
0         coihaique -45.58  -72.07      CL   
3       santa maria -29.68  -53.81      BR   
6         springbok -29.66   17.89      ZA   
10           albany  42.60  -73.97      US   
11        carnarvon -24.87  113.63      AU   
..              ...    ...     ...     ...   
594   saint andrews  34.05  -81.13      US   
595           basco  20.45  121.97      PH   
596           farah  32.50   62.50      AF   
597  campbell river  50.02 -125.24      CA   
599        westport  41.14  -73.36      US   

                                    hotels  
0               Diego De Almagro Coyhaique  
3                            Hotel Morotin  
6                     Faithful Guest Lodge  
10                                          
11                   Hospitality Carnarvon  
..                                     ...  
594  Baymont by Wyndham Columbia Northwest  
595                      Nathaniel's Lodge  
596                                         
597       Ramada by Wyndham Campbell River  
599                       The Westport Inn  

[229 rows x 5 columns]

In [11]:
# NOTE: Do not change any of the code in this cell

# Using the template add the hotel marks to the heatmap
info_box_template = """
<dl>
<dt>Name</dt><dd>{hotels}</dd>
<dt>City</dt><dd>{City}</dd>
<dt>Country</dt><dd>{Country}</dd>
</dl>
"""
# Store the DataFrame Row
# NOTE: be sure to update with your DataFrame name
hotel_info = [info_box_template.format(**row) for index, row in hotel_df.iterrows()]
locations = hotel_df[["Lat","Lng"]]

In [12]:
# Add marker layer ontop of heat map
marker_layer = gmaps.marker_layer(locations, info_box_content=hotel_info)
fig.add_layer(marker_layer)


# Display Map
fig

Figure(layout=FigureLayout(height='420px'))